In [59]:
import json
import nltk
from nltk.corpus import wordnet as wn
from nltk.stem.wordnet import WordNetLemmatizer
nltk.download('wordnet')
from nltk.corpus import words
nltk.download('words')
ww = words.words()

[nltk_data] Downloading package wordnet to /home/sy/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package words to /home/sy/nltk_data...
[nltk_data]   Package words is already up-to-date!


In [154]:
def format(s):
    return ' '.join(s.split('_'))

In [229]:
from collections import defaultdict
dsynonyms = defaultdict(set)
n=0

for word in wn.words():
    n+=1
    synsets = wn.synsets(word)
    synonymss = wn.synonyms(word)
    syns = set()
    for synset, synonyms in zip(synsets, synonymss):
        if synset.pos() in ['a', 's']:
            syns |= set(synonyms)
    if len(syns) >= 4:
        clues = [format(clue) for clue in syns]
        ok = True
        for clue in clues:
            if clue in dsynonyms:
                ok = False
        if ok:
            clues.append(format(word))
            dsynonyms[word] = dict(group=f'synonyms for {format(word)}', clues=clues)

In [230]:
wn.synsets('genip')

[Synset('spanish_lime.n.01'), Synset('genip.n.02')]

In [231]:
# flag button for reporting

In [232]:
import pandas as pd

In [243]:
df = pd.read_csv('LADECv1-2019.csv', index_col=0)

In [244]:
df = df.drop(df[df.correctParse == 'no'].index)
df = df.drop(df[df.isCommonstim == 'no'].index)

In [235]:
prefixes = df.groupby('c1').groups
suffixes = df.groupby('c2').groups
pres = []
for prefix, ids in prefixes.items():
    if len(ids) >= 4:
        pres.append((prefix, list(df.loc[list(ids)].c2)))
sufs = []
for suffix, ids in suffixes.items():
    if len(ids) >= 4:
        sufs.append((suffix, list(df.loc[list(ids)].c1)))

In [236]:
dprefix = {}
for prefix, ids in pres:
    res = set()
    for id in ids:
        if (id[-1] == 's' and id[:-1] in ids) or (ids[-2:] == 'es' and ids[:-2] in ids):
            continue
        res.add(id)
    if len(res) < 4:
        continue
    dprefix[prefix] = dict(group=f'{prefix} _', clues=list(res))

dsuffix = {}
for suffix, ids in sufs:
    if (suffix[-1] == 's' and suffix[:-1] in dsuffix) or (suffix[-2:] == 'es' and suffix[:-2] in ids):
        #dsuffix[suffix[:-1]] = set(ids)
        continue
    if len(ids) < 4:
        continue
    dsuffix[suffix] = dict(group=f'_ {suffix}', clues=ids)

In [237]:
from Levenshtein import ratio
def similar(a, b):
    return ratio(a, b) >= .8
import inflect

p = inflect.engine()

def normalize(w):
    pass

def filter_duplicates(group):
    if not group:
        return []
    ok = [group[0]]
    for i in range(1, len(group)):
        for word in ok:
            if similar(word, group[i]):
                break
        else:
            ok.append(group[i])
    return ok

In [238]:
blacklist = ['man', 'men', 'woman', 'women']

In [239]:

def process_corpus(corpus):
    new = {}
    for word, group in corpus.items():
        clues = group['clues']
        clues = [clue for clue in clues if clue not in blacklist]
        clues = filter_duplicates(clues)
        if len(clues) < 4:
            continue
        new[word] = dict(group=group['group'], clues=clues)
    return new

In [240]:
corpus = {**dprefix}
corpus.update(dsuffix)
corpus.update(dsynonyms)
filtered_corpus = process_corpus(corpus)

In [259]:
print(len(dprefix), len(dsuffix))

437 330


In [241]:

with open('../static/corpus.js', 'w') as f:
    f.write('var corpus = ')
    json.dump(filtered_corpus, f)

In [242]:
wn.synonyms('encroaching')

[['encroach', 'impinge', 'infringe'],
 ['encroach', 'entrench', 'impinge', 'trench'],
 ['invasive', 'trespassing']]

In [252]:
df[['c1', 'c2', 'stim', 'isCommonC1', 'isCommonC2', 'isCommonstim']]

c1     c2        stim  isCommonC1  isCommonC2  isCommonstim
id_master                                                                
3237         gad  about    gadabout           1           1             1
4592       knock  about  knockabout           1           1             1
8231        turn  about   turnabout           1           1             1
6139        race  about   raceabout           1           1             0
8331        walk  about   walkabout           1           1             1
...          ...    ...         ...         ...         ...           ...
4515        junk  yards   junkyards           1           0             0
6812        ship  yards   shipyards           1           0             0
2667        farm  yards   farmyards           1           0             0
1007       brick  yards  brickyards           1           0             0
8892         zig    zag      zigzag           0           0             1

[8372 rows x 6 columns]

In [258]:
df[df.c2=='fare'][['c1', 'c2', 'stim', 'isCommonC1', 'isCommonC2', 'isCommonstim']]

c1    c2       stim  isCommonC1  isCommonC2  isCommonstim
id_master                                                              
8361         war  fare    warfare           1           1             1
2715       field  fare  fieldfare           1           1             0
1298         car  fare    carfare           1           1             1
51           air  fare    airfare           1           1             1